# Your Title Here

**Name(s)**: Ethan Arnn

**Website Link**: (your website link)

In [ ]:
import pandas as pd
import numpy as np
from pathlib import Path

import plotly.express as px
pd.options.plotting.backend = 'plotly'

from dsc80_utils import * # Feel free to uncomment and use this.

## Step 1: Introduction

Currently I want to explore making predictions on what role a player played given their post-game data. 

In [18]:
lol_fp = Path('data') / '2022_LoL_data.csv'
lol = pd.read_csv(lol_fp)
lol

/var/folders/9k/jmm192cd4qgfwgw8kn2fwkfm0000gn/T/ipykernel_48524/3089127226.py:2: DtypeWarning:

Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.



gameid datacompleteness  \
0       ESPORTSTMNT01_2690210         complete   
1       ESPORTSTMNT01_2690210         complete   
2       ESPORTSTMNT01_2690210         complete   
...                       ...              ...   
150585       9687-9687_game_5          partial   
150586       9687-9687_game_5          partial   
150587       9687-9687_game_5          partial   

                                                url league  ...  deathsat25  \
0                                               NaN   LCKC  ...         1.0   
1                                               NaN   LCKC  ...         2.0   
2                                               NaN   LCKC  ...         0.0   
...                                             ...    ...  ...         ...   
150585  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   
150586  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   
150587  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   

       opp_killsat25  opp_assistsat25 opp_deathsat25  
0                0.0              2.0            0.0  
1                1.0              5.0            1.0  
2                3.0              4.0            3.0  
...              ...              ...            ...  
150585           NaN              NaN            NaN  
150586           NaN              NaN            NaN  
150587           NaN              NaN            NaN  

[150588 rows x 164 columns]

## Step 2: Data Cleaning and Exploratory Data Analysis

In [19]:
# Firstly, since my questions concerns prediction what role a player played based
# on their post-game stats, I want to remove the rows containing summary data for
# the teams.

lol_individual = lol[lol['position'] != 'team']
lol_individual.shape

(125490, 164)

In [20]:
lol_individual.head()

gameid datacompleteness  url league  ...  deathsat25  \
0  ESPORTSTMNT01_2690210         complete  NaN   LCKC  ...         1.0   
1  ESPORTSTMNT01_2690210         complete  NaN   LCKC  ...         2.0   
2  ESPORTSTMNT01_2690210         complete  NaN   LCKC  ...         0.0   
3  ESPORTSTMNT01_2690210         complete  NaN   LCKC  ...         2.0   
4  ESPORTSTMNT01_2690210         complete  NaN   LCKC  ...         2.0   

  opp_killsat25  opp_assistsat25 opp_deathsat25  
0           0.0              2.0            0.0  
1           1.0              5.0            1.0  
2           3.0              4.0            3.0  
3           3.0              4.0            0.0  
4           0.0              7.0            2.0  

[5 rows x 164 columns]

#### **Univariate Analysis:**

In [21]:
wards_plot = px.box(lol_individual, x='position', y='wpm')
wards_plot.show()
#support players have significantly higher wards per minute

In [22]:
dmg_taken_plot = px.box(lol_individual, x='position', y='damagetakenperminute')
dmg_taken_plot.show()
#jungle has a significantly higher damage taken, with top and mid follwing behind

In [23]:
dmg_mitigated_plot = px.box(lol_individual, x='position', y='earned gpm')
dmg_mitigated_plot.show()
# bottom lane highest...

In [24]:
minion_kills_plot = px.box(lol_individual, x='position', y='cspm')
minion_kills_plot.show()
#hardest challenge will be differentiating top, mid, and bot lanes

## Step 3: Assessment of Missingness

## Step 4: Hypothesis Testing

Null hypothesis: There is no difference between the average damageshare of top lane players and the average damageshare of midlane players

Alternative hypothesis: The average damageshare of midlane players is larger than the average damageshare of top lane players

In [25]:
# I want to test whether the damageshare for top and midlane characters is the same or not. That way I can determine if this is a good feature to use in a model
# for classifying positions.

top_dmgshare_avg = lol_individual[lol_individual['position'] == 'top']['damageshare'].mean()
print(top_dmgshare_avg)

mid_dmgshare_avg = lol_individual[lol_individual['position'] == 'mid']['damageshare'].mean()
print(mid_dmgshare_avg)

observed_diff = top_dmgshare_avg - mid_dmgshare_avg
observed_diff


0.2352230817022633
0.2609270147513549


np.float64(-0.025703933049091576)

In [26]:
# lol_top_mid = lol_individual[(lol_individual['position'] == 'top')
#                               | (lol_individual['position'] == 'mid')]

# differences = []
# n = 1000

# for _ in range(n):

#     shuffled_positions = np.random.permutation(lol_top_mid['position'])
#     lol_top_mid['shuffled_positions'] = shuffled_positions

#     top_perm_avg = lol_top_mid[lol_top_mid['shuffled_positions'] == 'top']['damageshare'].mean()
#     mid_perm_avg = lol_top_mid[lol_top_mid['shuffled_positions'] == 'mid']['damageshare'].mean()

#     differences.append(top_perm_avg - mid_perm_avg)

# p_value = sum([diff <= observed_diff for diff in differences]) / n
# p_value

Our p_value is 0 which is statistically significant at the 0.05 level. This means that damageshare could be a useful to predicting whether a player is top or mid.

In [27]:
# Now we will perform a permutation test by shuffling the top and midlane labels and calculating the various damageshare averages

## Step 5: Framing a Prediction Problem

##### For the prediction problem, I will be prediction what role someone played in a League of Legends match given their end-game stats. This will be a multi-class classification problem. I plan on using a Random Forest model, and using F1-score to evaluate my model.

## Step 6: Baseline Model

In [28]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier

In [29]:
X = lol_individual[['wpm', 'champion', 'damageshare']]
y = lol_individual['position']

x_train, x_test, y_train, y_test = test_train_split(X, y)

NameError: name 'test_train_split' is not defined

In [ ]:
pl = make_pipeline()

NameError: name 'make_pipeline' is not defined

## Step 7: Final Model

In [ ]:
# TODO

## Step 8: Fairness Analysis

In [ ]:
# TODO